<a href="https://colab.research.google.com/github/Some7hing0riginal/lighthouselabs-midterm1/blob/main/Light%20version%20of%20Weather.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd

Error: Session cannot generate requests

In [ ]:
df = pd.read_csv("../data/flights_2019.csv", nrows=5048576)

In [ ]:
df[["origin" ,"dest"]].values

Error: Session cannot generate requests

In [ ]:
df[["origin" ,"dest"]].values.ravel()

array(['PHL', 'ITH', 'CAE', ..., 'SEA', 'SEA', 'PDX'], dtype=object)

In [ ]:
airports = pd.unique(df[["origin" ,"dest"]].values.ravel())

In [ ]:
airports

array(['PHL', 'ITH', 'CAE', 'CLT', 'DCA', 'MYR', 'BHM', 'ILM', 'ROC',
       'GPT', 'HPN', 'VPS', 'LEX', 'SAV', 'OAJ', 'CVG', 'CHS', 'CAK',
       'GSO', 'PHX', 'RAP', 'OKC', 'ORD', 'SDF', 'FAT', 'LAX', 'MHK',
       'DFW', 'DSM', 'EUG', 'BNA', 'TVC', 'DEN', 'GCC', 'LAW', 'MCI',
       'DTW', 'SAF', 'HOU', 'TYS', 'MLU', 'DAY', 'FWA', 'COU', 'GJT',
       'YUM', 'TUS', 'CLL', 'SBN', 'GRB', 'IND', 'MKE', 'GRR', 'CLE',
       'BRO', 'ALB', 'ASE', 'SYR', 'SHV', 'FSD', 'SLC', 'MLI', 'SGF',
       'ROW', 'BWI', 'FNT', 'FLG', 'BTV', 'MFR', 'CMH', 'MHT', 'SJC',
       'PDX', 'SMF', 'SAN', 'STS', 'DAL', 'SEA', 'AUS', 'PSP', 'SFO',
       'OMA', 'BOI', 'BUR', 'SNA', 'ABQ', 'MSP', 'RNO', 'OAK', 'BZN',
       'MRY', 'IAD', 'PSC', 'LGA', 'FAR', 'SUN', 'ATW', 'LIT', 'CID',
       'ATL', 'LAS', 'JFK', 'MDW', 'SAT', 'MGM', 'BIS', 'MOB', 'MSO',
       'BIL', 'GFK', 'GTF', 'DLH', 'FSM', 'BOS', 'PIA', 'VLD', 'MBS',
       'CHA', 'RST', 'IAH', 'AVP', 'ORF', 'ERI', 'GTR', 'RDM', 'TRI',
       'GNV', 'ICT',

In [ ]:
len(airports)

373

In [ ]:
import requests
"""
Returns the weather for a given airport from start date to end date
"""
def getWeather(airport, startDate, endDate):
    base_url = "http://api.worldweatheronline.com/premium/v1/{api}"
    endpoint = base_url.format(api="past-weather.ashx")
    parameters = {'key': "3a8f45681ad5411ea11175411212010", 
                'q': airport, 
                'format': 'json', 
                'date' : startDate,
                "enddate": endDate,
                "tp" : "1"}

    response = requests.get(endpoint, params=parameters)
    return response

response = getWeather("DFW", "2013-04-21", "2013-07-21")

In [ ]:
response.status_code

200

In [ ]:
responeJson = response.json()

In [ ]:
import uuid
from IPython.display import display_javascript, display_html, display
import json

class RenderJSON(object):
    def __init__(self, json_data):
        if isinstance(json_data, dict):
            self.json_str = json.dumps(json_data)
        else:
            self.json_str = json_data
        self.uuid = str(uuid.uuid4())

    def _ipython_display_(self):
        display_html('<div id="{}" style="height: 600px; width:100%;"></div>'.format(self.uuid), raw=True)
        display_javascript("""
        require(["https://rawgit.com/caldwell/renderjson/master/renderjson.js"], function() {
        document.getElementById('%s').appendChild(renderjson(%s))
        });
        """ % (self.uuid, self.json_str), raw=True)

In [ ]:
RenderJSON(responeJson)

In [ ]:
dates = responeJson["data"]["weather"]

dates

In [ ]:
for entry in dates:
    print(entry["date"])

In [ ]:
for airport in airports:
    print(airport)

In [ ]:
import time
import json

"""
{'DFW' : {'2013-04-21' : { avgTemp : 23, humidity: 25, etc}}}

The weather API only supports maximum of 35 days of data at a time. We need to
load data at that rate (5 weeks at a time)
"""

def formatWeather(airport, startDate, endDate):
    formattedDict = {}
    #put sleep in to not DDOS the server
    time.sleep(0.1)
    formattedDict[airport] = {}
    response = getWeather(airport, startDate, endDate)
    if response.status_code != 200:
        #something went wrong, print the contents for logging
        print(response.content)
        return formattedDict

    responseJson = response.json()

    datesData = responseJson["data"]["weather"]


    for entry in datesData:
        hourlies = {}
        for hourly in entry["hourly"]:
            hourlies.update({hourly["time"] : {
                        "humidity" : hourly["humidity"],
                        "tempC" : hourly["tempC"],
                        "windspeedKmph" : hourly["windspeedKmph"],
                        "weatherCode" : hourly["weatherCode"],
                        "precipMM" : hourly["precipMM"],
                        "visibility" : hourly["visibility"],
                        "pressure" : hourly["pressure"],
                        "WindGustKmph" : hourly["WindGustKmph"],
                        "winddirDegree" : hourly["winddirDegree"],
                        "winddir16Point" : hourly["winddir16Point"],
                        "cloudcover" : hourly["cloudcover"],
                        "FeelsLikeC" : hourly["FeelsLikeC"],
                        "uvIndex" : hourly["uvIndex"],
                        "weatherDesc" : hourly["weatherDesc"][0]["value"]
                        }
            })
        formattedDict[airport][entry["date"]] = {
                        "avgtempC" : entry["avgtempC"],
                        "uvIndex" : entry["uvIndex"],
                        "totalSnow_cm" : entry["totalSnow_cm"],
                        'sunHour': entry["sunHour"],
                        'maxtempC' : entry["maxtempC"],
                        'mintempC' : entry["mintempC"],
                        "time" : hourlies,
                        "astronomy" : entry["astronomy"]
                        } 

                        # "humidity" : entry["hourly"][0]["humidity"],
                        # "tempC" : entry["hourly"][0]["tempC"],
                        # "windspeedKmph" : entry["hourly"][0]["windspeedKmph"],
                        # "weatherCode" : entry["hourly"][0]["weatherCode"],
                        # "precipMM" : entry["hourly"][0]["precipMM"],
                        # "visibility" : entry["hourly"][0]["visibility"],
                        # "pressure" : entry["hourly"][0]["pressure"],
                        # "WindGustKmph" : entry["hourly"][0]["WindGustKmph"],
                        # "winddirDegree" : entry["hourly"][0]["winddirDegree"],
                        # "winddir16Point" : entry["hourly"][0]["winddir16Point"],
                        # "cloudcover" : entry["hourly"][0]["cloudcover"],
                        # "FeelsLikeC" : entry["hourly"][0]["FeelsLikeC"],
                        # "weatherDesc" : entry["hourly"][0]["weatherDesc"][0]["value"]
                        
                        #}
    return formattedDict
                


formattedDict = formatWeather("DFW", "2019-01-01", "2019-12-31")


In [ ]:
RenderJSON(formattedDict)

In [ ]:
formatWeather("DFW", "2019-02-01", "2019-03-01")

In [ ]:
def MergeDict(dict1, dict2):
    res = {**dict1, **dict2}
    return res

In [ ]:
#conda install -c conda-forge mergedeep
from mergedeep import merge
secondMonth = formatWeather("DFW", "2019-02-01", "2019-03-01")
merge(formattedDict, secondMonth) 


In [ ]:
RenderJSON(formattedDict)

In [ ]:
from datetime import datetime, timedelta
import mergedeep
"""
This function will retrieve weather data for a specified airport at 34 day increments 
until end date
"""
def getWeatherData(airport, startDate, endDate):
    startDate_object = datetime.strptime(startDate, "%Y-%m-%d")
    endDate_object = datetime.strptime(endDate, "%Y-%m-%d")
    monthlyDelta = timedelta(days=34)
    formattedDict = {}

    while startDate_object <= endDate_object:
        startDate = str(startDate_object).split()[0]
        print(str(startDate_object))
        startDate_object = startDate_object + monthlyDelta
        endDate = str(startDate_object).split()[0]
        print(str(startDate_object))

        secondMonth = formatWeather(airport, startDate, endDate)
        mergedeep.merge(formattedDict, secondMonth) 
    
    return formattedDict

dfwWeather = getWeatherData("DFW", "2019-01-01", "2019-12-31")

2019-01-01 00:00:00
2019-02-04 00:00:00
2019-02-04 00:00:00
2019-03-10 00:00:00
2019-03-10 00:00:00
2019-04-13 00:00:00
2019-04-13 00:00:00
2019-05-17 00:00:00
2019-05-17 00:00:00
2019-06-20 00:00:00
2019-06-20 00:00:00
2019-07-24 00:00:00
2019-07-24 00:00:00
2019-08-27 00:00:00
2019-08-27 00:00:00
2019-09-30 00:00:00
2019-09-30 00:00:00
2019-11-03 00:00:00
2019-11-03 00:00:00
2019-12-07 00:00:00
2019-12-07 00:00:00
2020-01-10 00:00:00


In [ ]:
dfwWeather
RenderJSON(dfwWeather)

In [ ]:
import json
import mergedeep
weatherDatabase2019 = {}
for airport in airports:
    print(airport)
    mergedeep.merge(weatherDatabase2019, getWeatherData(airport, "2019-01-01", "2019-12-31"))


with open('weatherDB2019.json', 'w') as fp:
    json.dump(weatherDatabase2019, fp)

In [ ]:
RenderJSON(weatherDatabase2019)

NameError: name 'weatherDatabase2019' is not defined

In [ ]:
import json
with open('weatherDB2019.json', 'r') as fp:
    weatherDatabase2019 = json.load(fp)



In [ ]:
weatherDatabase2019["BQK"]

{}

In [ ]:
BQKData = getWeatherData("BQK", "2019-01-01", "2019-12-31")

2019-01-01 00:00:00
2019-02-04 00:00:00
2019-02-04 00:00:00
2019-03-10 00:00:00
2019-03-10 00:00:00
2019-04-13 00:00:00
2019-04-13 00:00:00
2019-05-17 00:00:00
2019-05-17 00:00:00
2019-06-20 00:00:00
2019-06-20 00:00:00
2019-07-24 00:00:00
2019-07-24 00:00:00
2019-08-27 00:00:00
2019-08-27 00:00:00
2019-09-30 00:00:00
2019-09-30 00:00:00
2019-11-03 00:00:00
2019-11-03 00:00:00
2019-12-07 00:00:00
2019-12-07 00:00:00
2020-01-10 00:00:00


In [ ]:
RenderJSON(BQKData)

In [ ]:
import mergedeep
weatherDatabase2019.update(BQKData)

In [ ]:
weatherDatabase2019["BQK"]

In [ ]:
airports[110]

NameError: name 'airports' is not defined

In [ ]:
for airport in airports[110:]: